In [1]:
import mkl_data_processing as mkldp
import os
import pickle
import pandas as pd
import sys
import sys
from memory_profiler import profile
import pandas as pd
import numpy as np
import gc
sys.path.append('/home/ak/Documents/Research/PaperCode/singlekernelclf/')
import jsonpickle
from MKLpy.preprocessing import normalization, rescale_01
from MKLpy.metrics import pairwise
from MKLpy import generators
from MKLpy.algorithms import AverageMKL, EasyMKL
from sklearn.svm import SVC
from collections import OrderedDict
import os
from sklearn.metrics import accuracy_score
import torch
from MKLpy.model_selection import cross_val_score
from MKLpy.multiclass import OneVsRestMKLClassifier, OneVsOneMKLClassifier

from MKLpy.algorithms import AverageMKL, EasyMKL, \
    KOMD, HeuristicMKL, PWMK, FHeuristic, CKA  # KOMD is not a MKL algorithm but a simple kernel machine like the SVM

from fileutils import new_feature_utils as nfu
from fileutils.new_feature_utils import CreateMarketFeatures
import multiprocessing

from collections import defaultdict
import os
import multiprocessing
import psutil
import pickle
from collections import defaultdict
import itertools
import time

from MKLpy.scheduler import ReduceOnWorsening
from MKLpy.callbacks import EarlyStopping



In [2]:
import matplotlib.pyplot as plt  # This is python's popular plotting library.
# This is to ensure matplotlib plots inline and does not try to open a new window.
%matplotlib inline  
# Show the tensor.
def showTensor(aTensor):
    plt.figure()
    plt.imshow(aTensor.numpy())
    plt.colorbar()
    plt.show()
    



In [3]:
from fileutils import DataLoader as DataLoader
from fileutils import paths
from fileutils import new_feature_utils as nfu
from fileutils.new_feature_utils import CreateMarketFeatures

In [4]:
def open_pickle_filepath(pickle_file):
    pickle_to_file = pickle.load(open(pickle_file, "rb"), encoding='latin1')

    return pickle_to_file


def forward_Dates(list_of_keys, current_date):
    """
    return all the forward looking dates for each idxKey we use for training

    :param list_of_keys: dates i have model dates for out of sample
    :param current_date: current model date
    :return: forward dates for applying the fitted model
    """
    lookAheadKeys = sorted(i for i in list_of_keys if i > current_date)
    return lookAheadKeys


def logmemoryusage(msg):
    # function to log memory usage
    process = psutil.Process(os.getpid())
    print('Memory usage at %s is %smb.' % (msg, process.memory_info().rss / 1000 / 1000))



In [7]:
os.listdir(commonLocs)

['LabelsAlternateThree',
 'FittedModelsAprilModels2021',
 'LabelsAlternateFour',
 'LabelsAlternateSeven',
 'FittedModels',
 'Labels_AlternateApril2021',
 'processedSingleKernelOOS',
 'LabelsAlternateOne',
 'LabelsAlternateSix',
 'CrossValidationResults',
 'OOSPredictions',
 'MKLOOSPredictionsApril2021',
 'LabelsAlternateTwo',
 'MKLFittedModels',
 'LabelAnalysisResults',
 'JointLocationsDicts',
 'LabelsAlternateFive',
 'MKLOOSPredictions']

In [6]:
mainPath = mkldp.paths('main')

symbols = sorted(os.listdir(mkldp.paths('symbols_features')))
jointFeatureLocation = os.path.join(mainPath, "ExperimentCommonLocs/JointLocationsDicts")
commonLocs  = os.path.join(mainPath, "ExperimentCommonLocs/")
# common locs contains a lot of folders, including the prediction targets and the rest

mklOOSPredictionPath = os.path.join(mainPath, "ExperimentCommonLocs/MKLOOSPredictions")
allFiles = os.listdir(jointFeatureLocation)
fittedModelsPath = os.path.join(mainPath, "ExperimentCommonLocs/FittedModels")
oosPredictionsPath = os.path.join(mainPath, "ExperimentCommonLocs/OOSPredictions")

In [16]:
mainPath = mkldp.paths('main')
mainPath

'/media/ak/DataOnly/'

In [10]:
file = allFiles[0]    
select_file_path = os.path.join(jointFeatureLocation, file)  # formulate the path

In [11]:
unpickled_select_file = open_pickle_filepath(select_file_path) 

In [14]:
keys = list(unpickled_select_file.keys())
unpickled_select_file[keys[0]]

{'20170117': ['/media/ak/DataOnly/SymbolFeatureDirectories/AZN.L/MODEL_BASED/20170116/AZN.L_3_states_features_date:_20170117_now:_20181228_.pickle',
  '/media/ak/DataOnly/ExperimentCommonLocs/LabelsAlternateSeven/AZN.L/20170117.csv'],
 '20170118': ['/media/ak/DataOnly/SymbolFeatureDirectories/AZN.L/MODEL_BASED/20170116/AZN.L_3_states_features_date:_20170118_now:_20181228_.pickle',
  '/media/ak/DataOnly/ExperimentCommonLocs/LabelsAlternateSeven/AZN.L/20170118.csv'],
 '20170119': ['/media/ak/DataOnly/SymbolFeatureDirectories/AZN.L/MODEL_BASED/20170116/AZN.L_3_states_features_date:_20170119_now:_20181228_.pickle',
  '/media/ak/DataOnly/ExperimentCommonLocs/LabelsAlternateSeven/AZN.L/20170119.csv'],
 '20170120': ['/media/ak/DataOnly/SymbolFeatureDirectories/AZN.L/MODEL_BASED/20170116/AZN.L_3_states_features_date:_20170120_now:_20181228_.pickle',
  '/media/ak/DataOnly/ExperimentCommonLocs/LabelsAlternateSeven/AZN.L/20170120.csv'],
 '20170123': ['/media/ak/DataOnly/SymbolFeatureDirectories/A

In [47]:
labelsAlternateLocs = {f:os.path.join(commonLocs, f) for f in os.listdir(os.path.join(mainPath, "ExperimentCommonLocs/")) if str("LabelsAlternate") in f }
labelKeys = list(labelsAlternateLocs.keys())
alternate_labels_nos = {1:"LabelsAlternateOne", 2:"LabelsAlternateTwo", 3:"LabelsAlternateThree", 
                        4:"LabelsAlternateFour", 5:"LabelsAlternateFive", 6:"LabelsAlternateSix"}  # we have 7 alternative data types



In [272]:
symbol_idx = 16  # pick a symbol
symbol = sorted(symbols)[symbol_idx]  # to be serialised so read all the symbols
print(symbol)

symbolData = DataLoader(mainPath, symbol)  # initiate a path where all the data should be


LAND.L


In [129]:
label_idx = 3  # to be serialised

labelsLocation = labelsAlternateLocs[alternate_labels_nos[label_idx]]

labelsLocation = os.path.join(labelsLocation, symbol)
# testFile = os.path.join(labelsLocation, os.listdir(labelsLocation)[1])

In [130]:
pd.read_csv(testFile)

Unnamed: 0       TradedTime  TradedPrice  ReturnTradedPrice   Volume  \
0            0  08:04:59.233104     0.013737           0.000000   5275.0   
1            1  08:06:45.483196     0.013859           0.008805   5000.0   
2            2  08:40:08.863746     0.013761          -0.007073   2000.0   
3            3  08:41:16.382532     0.013737          -0.001732   3000.0   
4            4  08:52:50.386457     0.013807           0.005046   2172.0   
..         ...              ...          ...                ...      ...   
77          77  15:25:35.883440     0.013975           0.000000   1162.0   
78          78  15:25:35.883500     0.013975           0.000000   1397.0   
79          79  15:25:35.883512     0.014000           0.001787  18750.0   
80          80  15:26:40.771196     0.013900          -0.007168  50000.0   
81          81  15:35:22.601223     0.014075           0.012511   1064.0   

       Duration  label_MovAv__window_8__thres_arbitrary__0.0  
0      0.000000                                          1.0  
1    106.250092                                         -1.0  
2   2003.380550                                          1.0  
3     67.518786                                          1.0  
4    694.003925                                          1.0  
..          ...                                          ...  
77     2.768883                                          NaN  
78     0.000060                                          NaN  
79     0.000012                                          NaN  
80    64.887684                                          NaN  
81   521.830027                                          NaN  

[82 rows x 7 columns]

In [131]:
print(labelsLocation)
files = os.listdir(jointFeatureLocation)
fileIdx =2
pickle_path = os.path.join( jointFeatureLocation, [f for f in os.listdir(jointFeatureLocation) if str(symbol) in f][fileIdx])

/media/ak/DataOnly/ExperimentCommonLocs/LabelsAlternateThree/LAND.L


In [132]:
label_idx

3

In [133]:
start_time = time.time()
for hmm_date_idx, hmm_date in enumerate(sorted(symbolData.hmm_dates_list)):

    hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
    symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
                            f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
    keys = sorted(list(symbol_feature_paths.keys()))
    print('########',hmm_date,'###########')
    print(keys)
    print('###############################')
    for key in keys:
        labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv")
        best_mkl_dict = defaultdict(dict)
        problem_dict = defaultdict(dict)
        good_dict = defaultdict(dict)
        
        if os.path.isfile(labels_file_path):  # check that this is a real path
                    print("can train")
                    print(" reading labels")  # this is the labels path!
                    labels = pd.read_csv(labels_file_path)
                    label_name = str(labels.columns[labels.columns.str.contains(pat='label')].values[0])
                    print(symbol_feature_paths[key])  # this is the labels path! in the correct order !!!!
                    logmemoryusage("Before garbage collect")
                    hmm_features = nfu.hmm_features_df(open_pickle_filepath(symbol_feature_paths[key]))
                    if hmm_features.isnull().values.all():  # checking that the HMM features are actually not null
                        continue
                    else:  # if features not null then start moving on!
                        market_features_df = CreateMarketFeatures(
                            CreateMarketFeatures(
                                CreateMarketFeatures(df=CreateMarketFeatures(df=labels).ma_spread_duration())
                                    .ma_spread()).chaikin_mf()).obv_calc()  # market features dataframe

                        df_concat = pd.DataFrame(
                            pd.concat([hmm_features, market_features_df], axis=1, sort='False').dropna())

                        df = df_concat[df_concat[label_name].notna()]
                        df_final = df.drop(
                            columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', 'Volume',
                                     label_name])
                        y_train = df[df.columns[df.columns.str.contains(pat='label')]].iloc[:, 0]  # training labels
                        if df_final.shape[0] < 10:
                            print(' the ratio of classes is too low. try another label permutation')
                            problem_dict[hmm_date][key] =str(key)
                            continue
                        else:
                            try:
                                print("starting model fit") 
                                good_dict[hmm_date][key] = str(key)
                                
                            except ValueError:
                                continue
                                logmemoryusage("at the end")

        else:
                    print("#################### Your Labels File does not exist ----- ####")
        continue
        logmemoryusage("Before garbage collect")

current_time = time.time()

elapsed_time = current_time - start_time
print('elapsed time', elapsed_time)


######## 20170116 ###########
['20170117', '20170118', '20170119', '20170120', '20170123', '20170124', '20170125', '20170126', '20170127', '20170130', '20170131', '20170703', '20170704', '20170705', '20170706', '20170707', '20170710', '20170711', '20170712', '20170713', '20170714', '20170717', '20170718', '20170719', '20170720', '20170721', '20170724', '20170725', '20170726', '20170727', '20170728', '20170731', '20170801', '20170802', '20170803', '20170804', '20170807', '20170808', '20170809', '20170810', '20170811', '20170814', '20170815', '20170816', '20170817', '20170818', '20170821', '20170822', '20170823', '20170824', '20170825', '20170829', '20170830', '20170831', '20170901', '20170904', '20170905', '20170906', '20170907', '20170908', '20170911', '20170912', '20170913', '20170914', '20170915', '20170918', '20170919', '20170920', '20170921', '20170922', '20170925', '20170926', '20170927', '20170928', '20170929', '20171002', '20171003', '20171004', '20171005', '20171006', '20171009

/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170731_now:_20181224_.pickle
Memory usage at Before garbage collect is 521.33888mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170801_now:_20181224_.pickle
Memory usage at Before garbage collect is 521.33888mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170802_now:_20181224_.pickle
Memory usage at Before garbage collect is 521.33888mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170803_now:_20181224_.pickle
Memory usage at Before garbage collect is 521.33888mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/2

starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170920_now:_20181224_.pickle
Memory usage at Before garbage collect is 522.145792mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170921_now:_20181224_.pickle
Memory usage at Before garbage collect is 522.145792mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170922_now:_20181224_.pickle
Memory usage at Before garbage collect is 522.145792mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170925_now:_20181224_.pickle
Memory usage at Before garbage collect is 522.145792mb.
starting model fit
can train
 reading labels
/media/ak/DataO

starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180209_now:_20181224_.pickle
Memory usage at Before garbage collect is 531.337216mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180212_now:_20181224_.pickle
Memory usage at Before garbage collect is 531.337216mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180213_now:_20181224_.pickle
Memory usage at Before garbage collect is 531.337216mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180214_now:_20181224_.pickle
Memory usage at Before garbage collect is 531.337216mb.
starting model fit
can train
 reading labels
/media/ak/DataO

can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170124_now:_20181224_.pickle
Memory usage at Before garbage collect is 533.229568mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170125_now:_20181224_.pickle
Memory usage at Before garbage collect is 533.229568mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170126_now:_20181224_.pickle
Memory usage at Before garbage collect is 533.229568mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170127_now:_20181224_.pickle
Memory usage at Before garbage collect is 533.229568mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_2017013

...

can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180221/LAND.L_3_states_features_date:_20180413_now:_20181224_.pickle
Memory usage at Before garbage collect is 992.915456mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180221/LAND.L_3_states_features_date:_20180416_now:_20181224_.pickle
Memory usage at Before garbage collect is 992.915456mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180221/LAND.L_3_states_features_date:_20180417_now:_20181224_.pickle
Memory usage at Before garbage collect is 992.915456mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180221/LAND.L_3_states_features_date:_20180418_now:_20181224_.pickle
Memory usage at Before garbage collect is 992.915456mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180221/LAND.L_3_states_features_date:_2018041

can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180223/LAND.L_3_states_features_date:_20180418_now:_20181224_.pickle
Memory usage at Before garbage collect is 995.766272mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180223/LAND.L_3_states_features_date:_20180419_now:_20181224_.pickle
Memory usage at Before garbage collect is 995.893248mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180223/LAND.L_3_states_features_date:_20180420_now:_20181224_.pickle
Memory usage at Before garbage collect is 995.893248mb.
######## 20180226 ###########
['20180227', '20180228', '20180403', '20180404', '20180405', '20180406', '20180409', '20180410', '20180411', '20180412', '20180413', '20180416', '20180417', '20180418', '20180419', '20180420']
###############################
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180226

/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180228/LAND.L_3_states_features_date:_20180406_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180228/LAND.L_3_states_features_date:_20180409_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180228/LAND.L_3_states_features_date:_20180410_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180228/LAND.L_3_states_features_date:_20180411_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180228/LAND.L_3_states_features_date:_20180

######## 20180405 ###########
['20180406', '20180409', '20180410', '20180411', '20180412', '20180413', '20180416', '20180417', '20180418', '20180419', '20180420']
###############################
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180405/LAND.L_3_states_features_date:_20180406_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180405/LAND.L_3_states_features_date:_20180409_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180405/LAND.L_3_states_features_date:_20180410_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180405/LAND.L_3_states_features_date:_2018041

starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180410/LAND.L_3_states_features_date:_20180419_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180410/LAND.L_3_states_features_date:_20180420_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
starting model fit
######## 20180411 ###########
['20180412', '20180413', '20180416', '20180417', '20180418', '20180419', '20180420']
###############################
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180411/LAND.L_3_states_features_date:_20180412_now:_20181224_.pickle
Memory usage at Before garbage collect is 996.2946559999999mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180411/LAND.L_3_states_features_date

## trying for the parallelised version

In [261]:
def parallelised_version(key):
    labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv")
    best_mkl_dict = defaultdict(dict)
    problem_dict = defaultdict(dict)
    good_dict = defaultdict(dict)
    if os.path.isfile(labels_file_path):  # check that this is a real path
        print("can train")
        print(" reading labels")  # this is the labels path!
        labels = pd.read_csv(labels_file_path)
        label_name = str(labels.columns[labels.columns.str.contains(pat='label')].values[0])
        print(symbol_feature_paths[key])  # this is the labels path! in the correct order !!!!
        logmemoryusage("Before garbage collect")
        hmm_features = nfu.hmm_features_df(open_pickle_filepath(symbol_feature_paths[key]))
        if hmm_features.isnull().values.all():  # checking that the HMM features are actually not null
            print('problem')
        else:  # if features not null then start moving on!
            market_features_df = CreateMarketFeatures(CreateMarketFeatures(CreateMarketFeatures(df=CreateMarketFeatures(df=labels).ma_spread_duration()).ma_spread()).chaikin_mf()).obv_calc()  # market features dataframe

            df_concat = pd.DataFrame(
                pd.concat([hmm_features, market_features_df], axis=1, sort='False').dropna())

            df = df_concat[df_concat[label_name].notna()]
            df_final = df.drop(
                columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', 'Volume',
                         label_name])
            y_train = df[df.columns[df.columns.str.contains(pat='label')]].iloc[:, 0]  # training labels
            if df_final.shape[0] < 10:
                print(' the ratio of classes is too low. try another label permutation')
                problem_dict[hmm_date][key] =str(key)
            else:
                try:
                    print("starting model fit") 
                    good_dict[hmm_date][key] = str(key)

                except ValueError:
                    logmemoryusage("at the end")

    else:
        print("#################### Your Labels File does not exist ----- ####")

        logmemoryusage("Before garbage collect")


In [263]:
start_time = time.time()
for hmm_date_idx, hmm_date in enumerate(sorted(symbolData.hmm_dates_list)):

    hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
    symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
                            f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
    keys = sorted(list(symbol_feature_paths.keys()))
    print('########',hmm_date,'###########')
    print(keys)
    print('###############################')
    with multiprocessing.Pool(processes=2) as process_pool:
        process_pool.map(parallelised_version, keys)
#     for key in keys:
#         parallelised_version(key)
        
current_time = time.time()

elapsed_time = current_time - start_time
print('elapsed time', elapsed_time)


######## 20170116 ###########
['20170117', '20170118', '20170119', '20170120', '20170123', '20170124', '20170125', '20170126', '20170127', '20170130', '20170131', '20170703', '20170704', '20170705', '20170706', '20170707', '20170710', '20170711', '20170712', '20170713', '20170714', '20170717', '20170718', '20170719', '20170720', '20170721', '20170724', '20170725', '20170726', '20170727', '20170728', '20170731', '20170801', '20170802', '20170803', '20170804', '20170807', '20170808', '20170809', '20170810', '20170811', '20170814', '20170815', '20170816', '20170817', '20170818', '20170821', '20170822', '20170823', '20170824', '20170825', '20170829', '20170830', '20170831', '20170901', '20170904', '20170905', '20170906', '20170907', '20170908', '20170911', '20170912', '20170913', '20170914', '20170915', '20170918', '20170919', '20170920', '20170921', '20170922', '20170925', '20170926', '20170927', '20170928', '20170929', '20171002', '20171003', '20171004', '20171005', '20171006', '20171009

can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170731_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.577472mb.
starting model fit
can train
 reading labels
starting model fit
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170706_now:_20181224_.pickle
can train
Memory usage at Before garbage collect is 3001.69216mb.
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170801_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.577472mb.
starting model fit
can train
 reading labels
starting model fit
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170707_now:_20181224_.pickle
can train
Memory usage at Before garbage collect is 3001.69216mb.
 reading labels
/media/ak/DataOnly/SymbolFeature

starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170824_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.581568mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170918_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.868288mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170825_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.581568mb.
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20170919_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.868288mb.
starting model fit
can train
 reading labels
/media/ak/D

Memory usage at Before garbage collect is 3001.8273280000003mb.
starting model fit
can train
 reading labels
starting model fit
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180205_now:_20181224_.pickle
can train
Memory usage at Before garbage collect is 3002.118144mb.
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20171013_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.8273280000003mb.
starting model fit
can train
 reading labels
starting model fit
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180208_now:_20181224_.pickle
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170116/LAND.L_3_states_features_date:_20180206_now:_20181224_.pickle
Memory usage at Before garbage collect is 3001.8273280000003mb.
Memory usage at Before garbage coll

can train
can train
 reading labels
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170712_now:_20181224_.pickle
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170118_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.349248mb.
Memory usage at Before garbage collect is 2999.320576mb.
problem
can train
problem
 reading labels
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170713_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.6564479999997mb.
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170117/LAND.L_3_states_features_date:_20170119_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.6605440000003mb.
problem
can train
 reading labels
problem
can train
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L

...

problem
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180222/LAND.L_3_states_features_date:_20180418_now:_20181224_.pickle
problem
Memory usage at Before garbage collect is 2999.963648mb.
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180222/LAND.L_3_states_features_date:_20180416_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.873536mb.
problem
problem
can train
 reading labels
can train
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180222/LAND.L_3_states_features_date:_20180417_now:_20181224_.pickle
 reading labels
Memory usage at Before garbage collect is 2999.877632mb.
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180222/LAND.L_3_states_features_date:_20180419_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.963648mb.
problem
problem
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_B

problem
can train
 reading labels
problem
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180226/LAND.L_3_states_features_date:_20180417_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.9267839999998mb.
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180226/LAND.L_3_states_features_date:_20180419_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.9759360000003mb.
problem
can train
 reading labels
problem
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180226/LAND.L_3_states_features_date:_20180418_now:_20181224_.pickle
can train
Memory usage at Before garbage collect is 2999.9267839999998mb.
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180226/LAND.L_3_states_features_date:_20180420_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.9759360000003mb.
problem
problem
######## 20180227 ###########
['20180228', '20180403', '

can train
can train
 reading labels
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180403/LAND.L_3_states_features_date:_20180404_now:_20181224_.pickle
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180403/LAND.L_3_states_features_date:_20180406_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.537664mb.
Memory usage at Before garbage collect is 2999.5827200000003mb.
problem
can train
problem
 reading labels
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180403/LAND.L_3_states_features_date:_20180409_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.853056mb.
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180403/LAND.L_3_states_features_date:_20180405_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.88992mb.
problem
can train
 reading labels
problem
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectorie

/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180405/LAND.L_3_states_features_date:_20180420_now:_20181224_.pickle
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180405/LAND.L_3_states_features_date:_20180419_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.750656mb.
Memory usage at Before garbage collect is 2999.78752mb.
problem
problem
######## 20180406 ###########
['20180409', '20180410', '20180411', '20180412', '20180413', '20180416', '20180417', '20180418', '20180419', '20180420']
###############################
can train
can train
 reading labels
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180406/LAND.L_3_states_features_date:_20180411_now:_20181224_.pickle
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180406/LAND.L_3_states_features_date:_20180409_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.6032mb.
Memory usage at Before garbage collect is 299

can train
problem
 reading labels
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180411/LAND.L_3_states_features_date:_20180418_now:_20181224_.pickle
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180411/LAND.L_3_states_features_date:_20180419_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.9718399999997mb.
Memory usage at Before garbage collect is 2999.95136mb.
problem
problem
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180411/LAND.L_3_states_features_date:_20180420_now:_20181224_.pickle
Memory usage at Before garbage collect is 2999.9718399999997mb.
problem
######## 20180412 ###########
['20180413', '20180416', '20180417', '20180418', '20180419', '20180420']
###############################
can train
can train
 reading labels
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20180412/LAND.L_3_states_features_date:_20180413_now:_

In [267]:
# def outer_loop_function(hmm_date):
#     hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
#     symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
#                             f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
#     keys = sorted(list(symbol_feature_paths.keys()))
#     print('########',hmm_date,'###########')
#     print(keys)
#     print('###############################')
#     for key in keys:
#         labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv")
#         best_mkl_dict = defaultdict(dict)
#         problem_dict = defaultdict(dict)
#         good_dict = defaultdict(dict)
        
#         if os.path.isfile(labels_file_path):  # check that this is a real path
#                     print("can train")
#                     print(" reading labels")  # this is the labels path!
#                     labels = pd.read_csv(labels_file_path)
#                     label_name = str(labels.columns[labels.columns.str.contains(pat='label')].values[0])
#                     print(symbol_feature_paths[key])  # this is the labels path! in the correct order !!!!
#                     logmemoryusage("Before garbage collect")
#                     hmm_features = nfu.hmm_features_df(open_pickle_filepath(symbol_feature_paths[key]))
#                     if hmm_features.isnull().values.all():  # checking that the HMM features are actually not null
#                         continue
#                     else:  # if features not null then start moving on!
#                         market_features_df = CreateMarketFeatures(
#                             CreateMarketFeatures(
#                                 CreateMarketFeatures(df=CreateMarketFeatures(df=labels).ma_spread_duration())
#                                     .ma_spread()).chaikin_mf()).obv_calc()  # market features dataframe

#                         df_concat = pd.DataFrame(
#                             pd.concat([hmm_features, market_features_df], axis=1, sort='False').dropna())

#                         df = df_concat[df_concat[label_name].notna()]
#                         df_final = df.drop(
#                             columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', 'Volume',
#                                      label_name])
#                         y_train = df[df.columns[df.columns.str.contains(pat='label')]].iloc[:, 0]  # training labels
#                         if df_final.shape[0] < 10:
#                             print(' the ratio of classes is too low. try another label permutation')
#                             problem_dict[hmm_date][key] =str(key)
#                             continue
#                         else:
#                             try:
#                                 print("starting model fit") 
#                                 good_dict[hmm_date][key] = str(key)
                                
#                             except ValueError:
#                                 continue
#                                 logmemoryusage("at the end")

#         else:
#                     print("#################### Your Labels File does not exist ----- ####")
#         continue
#         logmemoryusage("Before garbage collect")

In [275]:
def outer_loop_function(hmm_date):
    # this is the usual loop but we are writing it as a function so I can parallelise it

    hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
    symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
                            f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
    keys = sorted(list(symbol_feature_paths.keys()))
    print('For hmm date: ', hmm_date, '###########')
    for key in keys:

        print('For key: ', key,'############')

        labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv")
        output_dict = defaultdict(dict)

        if os.path.isfile(labels_file_path):  # check that this is a real path
            print("can train")
            print(" reading labels")  # this is the labels path!
            labels = pd.read_csv(labels_file_path)
            label_name = str(labels.columns[labels.columns.str.contains(pat='label')].values[0])
            print(label_name)
            #print(symbol_feature_paths[key])  # this is the labels path! in the correct order !!!!
            logmemoryusage("Before garbage collect")
            hmm_features = nfu.hmm_features_df(open_pickle_filepath(symbol_feature_paths[key]))
            if hmm_features.isnull().values.all():  # checking that the HMM features are actually not null
                continue
                print('lots of NaNs on features')
            else:  # if features not null then start moving on!
                market_features_df = CreateMarketFeatures(
                    CreateMarketFeatures(
                        CreateMarketFeatures(df=CreateMarketFeatures(df=labels).ma_spread_duration())
                            .ma_spread()).chaikin_mf()).obv_calc()  # market features dataframe

                df_concat = pd.DataFrame(
                    pd.concat([hmm_features, market_features_df], axis=1, sort='False').dropna())

                df = df_concat[df_concat[label_name].notna()]
                df_final = df.drop(
                    columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', 'Volume',
                             label_name])
                y_train = df[df.columns[df.columns.str.contains(pat='label')]].iloc[:, 0]  # training labels
                if df_final.shape[0] < 10:
                    print(' the ratio of classes is too low. try another label permutation')
                    problem_dict[hmm_date][key] = str(key)
                    continue
                else:
                    try:
                        print("starting model fit")
                        Xtr,Xte,Ytr,Yte = train_test_split(df_final,y_train, test_size=.5, random_state=42)
                        # training
                        arrXtr = np.array(Xtr)
                        X_tr = normalization(rescale_01(arrXtr))
                        Y_tr = torch.Tensor(Ytr.values)

                        # testing

                        arrXte = np.array(Xte)
                        X_te = normalization(rescale_01(arrXte))
                        Y_te = torch.Tensor(Yte.values)

                        KLtr = [pairwise.homogeneous_polynomial_kernel(X_tr, degree=d) for d in range(1,21)] + [identity_kernel(len(Ytr))]
                        KLte = [pairwise.homogeneous_polynomial_kernel(X_te,X_tr, degree=d) for d in range(1,21)]
                        KLte.append(torch.zeros(KLte[0].size()))

                        print ('tuning lambda for EasyMKL...', end='')
                        base_learner = SVC(C=0.1)	#"soft"-margin svm
                        best_results = {}
                        for lam in [0.01, 0.1, 0.5, 0.9]:	#possible lambda values for the EasyMKL algorithm
                            #MKLpy.model_selection.cross_val_score performs the cross validation automatically, it may returns
                            #accuracy, auc, or F1 scores
                            scores = cross_val_score(KLtr, Ytr, EasyMKL(learner=base_learner, lam=lam), n_folds=5, scoring='accuracy')
                            acc = np.mean(scores)
                            if not best_results or best_results['score'] < acc:
                                best_results = {'lam' : lam, 'score' : acc}
                        #evaluation on the test set
                        from sklearn.metrics import accuracy_score
                        print ('done')
                        clf = EasyMKL(learner=base_learner, lam=best_results['lam']).fit(KLtr,Ytr)
                        y_pred = clf.predict(KLte)
                        accuracy = accuracy_score(Yte, y_pred)
                        print ('accuracy on the test set: %.3f, with lambda=%.2f' % (accuracy, best_results['lam']))


                    except ValueError:
                        continue
                        logmemoryusage("at the end")

        else:
            print("#################### Your Labels File does not exist ----- ####")
        continue
        logmemoryusage("Before garbage collect")

In [276]:
## testing the outerloop as well
start_time = time.time()

        


with multiprocessing.Pool(processes=2) as process_pool:
    process_pool.map(outer_loop_function, sorted(symbolData.hmm_dates_list))
current_time = time.time()
elapsed_time = current_time - start_time
print('elapsed time', elapsed_time)

For hmm date:  20170116 ###########
For hmm date:  20170710 ###########
For key:  20170117 ############
can train
 reading labels
For key:  20170711 ############
can train
label_MovAv__window_8__thres_arbitrary__0.0
 reading labels
Memory usage at Before garbage collect is 2998.21056mb.
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 2998.21056mb.
starting model fit
starting model fit
For hmm date:  20170802 ###########
For key:  20170803 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 2998.779904mb.
starting model fit
tuning lambda for EasyMKL...For hmm date:  20170825 ###########
For key:  20170829 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.313088mb.
For key:  20170830 ############
can train
 reading labels
For hmm date:  20170920 ###########
label_MovAv__window_8__thres_arbitrary__0.0

For key:  20171025 ############
can train
 reading labels
For key:  20180213 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.698112mb.
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3269.3698560000003mb.
For key:  20171026 ############
can train
 reading labels
For key:  20180214 ############
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.698112mb.
can train
 reading labels
For key:  20171027 ############
label_MovAv__window_8__thres_arbitrary__0.0
can train
Memory usage at Before garbage collect is 3269.3698560000003mb.
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.698112mb.
For key:  20180215 ############
can train
 reading labels
For key:  20171030 ############
label_MovAv__window_8__thres_arbitrary__0.0
can train
 reading labels
Memory usage at Before garbage 

For hmm date:  20180208 ###########
For key:  20180209 ############
can train
 reading labels
For key:  20180403 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3269.6811519999997mb.
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.947968mb.
For key:  20180404 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.947968mb.
starting model fit
For key:  20180405 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3076.947968mb.
For key:  20180406 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.1322880000002mb.
For key:  20180409 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage col

can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.554176mb.
For key:  20180411 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.7344mb.
For key:  20180412 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.7344mb.
For key:  20180413 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.7344mb.
For key:  20180416 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.7344mb.
For key:  20180417 ############
can train
 reading labels
label_MovAv__window_8__thres_arbitrary__0.0
Memory usage at Before garbage collect is 3077.7344mb.
For key:  20180418 ############
can train
 reading labels
label_MovAv__window_8__thres_a

Process ForkPoolWorker-278:
Process ForkPoolWorker-277:
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 108, in worker
    task = get()
  File "/usr/lib/python3.6/multiprocessing/queues.py", line 335, in get
    res = self._reader.recv_bytes()
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/connection.py", line 216, in recv_bytes
    buf = self._recv_bytes(maxlength)
  File "/usr/lib/python3.6/multiprocessing/connection.py", line 407, in _recv_bytes
    buf = self._recv(4)
  File "/usr/lib/python3.6/multiprocessing/connection.py", line 379, in _recv
    chunk = read(handle, remaining)
KeyboardInterrupt


tuning lambda for EasyMKL...

  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 108, in worker
    task = get()
  File "/usr/lib/python3.6/multiprocessing/queues.py", line 334, in get
    with self._rlock:
  File "/usr/lib/python3.6/multiprocessing/synchronize.py", line 95, in __enter__
    return self._semlock.__enter__()
KeyboardInterrupt


tuning lambda for EasyMKL...

KeyboardInterrupt: 

In [135]:
#elapsed time 132.99742126464844 - with dual loops
# with outer loop paralellised: elapsed time 103.9689884185791

defaultdict(dict, {})

In [277]:
hmmDatesList = sorted(symbolData.hmm_dates_list)
hmm_date_idx =2
hmm_date = hmmDatesList[hmm_date_idx]

hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
                        f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
keys = sorted(list(symbol_feature_paths.keys()))
print('########',hmm_date,'###########')

keyIdx = 3

labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv")
# this is the label path in older versions of the code

if os.path.isfile(labels_file_path):  # check that this is a real path
    print("can train")
    print(" reading labels")  # this is the labels path!
    labels = pd.read_csv(labels_file_path)
    label_name = str(labels.columns[labels.columns.str.contains(pat='label')].values[0])
    print(symbol_feature_paths[key])  # this is the labels path! in the correct order !!!!
    logmemoryusage("Before garbage collect")
    hmm_features = nfu.hmm_features_df(open_pickle_filepath(symbol_feature_paths[key]))


######## 20170118 ###########
can train
 reading labels
/media/ak/DataOnly/SymbolFeatureDirectories/LAND.L/MODEL_BASED/20170118/LAND.L_3_states_features_date:_20180420_now:_20181224_.pickle
Memory usage at Before garbage collect is 3119.140864mb.


In [284]:
if hmm_features.isnull().values.all():  # checking that the HMM features are actually not null
    print(' cant continue- full of NaNs')

else:  # if features not null then start moving on!
    market_features_df = CreateMarketFeatures(
        CreateMarketFeatures(
            CreateMarketFeatures(df=CreateMarketFeatures(df=labels).ma_spread_duration()).ma_spread()).chaikin_mf()).obv_calc()  # market features dataframe

    df_concat = pd.DataFrame(
        pd.concat([hmm_features, market_features_df], axis=1, sort='False').dropna())

    df = df_concat[df_concat[label_name].notna()]
    df_final = df.drop(
        columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', 'Volume',
                 label_name])
    y_train = df.reindex(columns =df.columns[df.columns.str.contains(pat='label')])
    if df_final.shape[0] < 10:
        print(' the ratio of classes is too low. try another label permutation')
    else:
        print(' good to go')



 good to go


In [145]:
labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv")

In [285]:
arrX = np.array(df_final)

In [286]:
''' feature normalisation'''
# feature scaling in [0,1] - X = rescale_01(arrX)
X = normalization(rescale_01(arrX))


In [287]:
X

tensor([[1.6756e-03, 3.5566e-01, 3.5566e-01,  ..., 1.7326e-01, 6.3221e-02,
         1.4632e-01],
        [1.5078e-03, 3.3945e-01, 3.3948e-01,  ..., 1.7675e-01, 6.4218e-02,
         1.4143e-01],
        [2.3174e-03, 3.3482e-01, 3.3491e-01,  ..., 1.8804e-01, 5.3700e-02,
         1.3917e-01],
        ...,
        [4.2159e-01, 6.0374e-04, 4.8391e-04,  ..., 1.5336e-01, 2.7385e-02,
         1.8413e-01],
        [4.0720e-01, 4.0963e-08, 0.0000e+00,  ..., 1.1449e-01, 2.4259e-02,
         1.7458e-01],
        [4.1856e-01, 0.0000e+00, 6.9123e-05,  ..., 9.9248e-02, 2.6253e-02,
         1.8092e-01]], dtype=torch.float64)

In [288]:
y_train

label_MovAv__window_8__thres_arbitrary__0.0
9                                            -1.0
10                                           -1.0
11                                           -1.0
12                                           -1.0
13                                            1.0
...                                           ...
1149                                          1.0
1150                                          1.0
1151                                          1.0
1152                                          0.0
1153                                          0.0

[1145 rows x 1 columns]

In [289]:
Y = torch.Tensor(y_train.values)

In [290]:
KLrbf = generators.RBF_generator(X, gamma=[.01, .1])

In [292]:
start_time = time.time()
base_learner = SVC(C=1)
clf = EasyMKL(lam=0.4, multiclass_strategy='ova', learner=base_learner).fit(KLrbf, Ytr)
#             # try ovo as
#             # well
mkl_avg = AverageMKL().fit(KLrbf, Y)

elapsed_time = current_time - start_time
print('elapsed time', elapsed_time)

ValueError: The kernel matrix and the labels vector are not aligned

In [161]:
clf.solution[0].weights

tensor([0.0867, 0.9133])

In [293]:

from sklearn.model_selection import train_test_split


from MKLpy.metrics import pairwise
from MKLpy.utils.misc import identity_kernel

In [294]:
Xtr,Xte,Ytr,Yte = train_test_split(df_final,y_train, test_size=.5, random_state=42)


In [295]:
arrXtr = np.array(Xtr)
X_tr = normalization(rescale_01(arrXtr))
Y_tr = torch.Tensor(Ytr.values)

In [296]:
arrXte = np.array(Xte)
X_te = normalization(rescale_01(arrXte))
Y_te = torch.Tensor(Yte.values)

In [297]:
KLtr = [pairwise.homogeneous_polynomial_kernel(X_tr, degree=d) for d in range(1,21)] + [identity_kernel(len(Ytr))]
KLte = [pairwise.homogeneous_polynomial_kernel(X_te,X_tr, degree=d) for d in range(1,21)]
KLte.append(torch.zeros(KLte[0].size()))


# MKL algorithms#

In [298]:

weights_OVA = dict()

print ('training EasyMKL with one-vs-all multiclass strategy...', end='')
from sklearn.svm import SVC
base_learner = SVC(C=0.5)
clfOVA = EasyMKL(lam=0.1, multiclass_strategy='ova', learner=base_learner).fit(KLtr,Y_tr)
from MKLpy.multiclass import OneVsRestMKLClassifier, OneVsOneMKLClassifier
print ('done')
print ('the combination weights are:')
# for sol in clf.solution:
#     print ('(%d vs all): ' % sol, clfOVA.solution[sol].weights)
#     weights_OVA[sol] = clfOVA.solution[sol].weights




training EasyMKL with one-vs-all multiclass strategy...done
the combination weights are:


In [299]:
pd.DataFrame(weights).median(axis=1)


0     0.000354
1     0.000635
2     0.000939
3     0.001291
4     0.001711
5     0.002217
6     0.002822
7     0.003533
8     0.004353
9     0.005250
10    0.006246
11    0.007345
12    0.008543
13    0.009838
14    0.011226
15    0.012704
16    0.014267
17    0.015912
18    0.017635
19    0.019432
20    0.853299
dtype: float32

In [300]:

#evaluate the solution
from sklearn.metrics import accuracy_score, roc_auc_score
import numpy as np
y_pred = clf.predict(KLte) #predictions
y_score = clf.decision_function(KLte) #rank
accuracy = accuracy_score(Y_te, y_pred)
print ('Accuracy score: %.3f' % (accuracy))



print ('training EasyMKL with one-vs-one multiclass strategy...', end='')
clf = EasyMKL(lam=1., multiclass_strategy='ovo', learner=base_learner).fit(KLtr,Y_tr)
print ('done')
print ('the combination weights are:')
weights_OVO = dict()
for sol in clf.solution:
    print ('(%d vs %d): ' % (sol[0], sol[1]), clf.solution[sol].weights)
    weights_OVO = clf.solution[sol].weights

(573, 3)
Accuracy score: 0.096
training EasyMKL with one-vs-one multiclass strategy...done
the combination weights are:
(-1 vs 0):  tensor([0.0500, 0.0634, 0.0648, 0.0625, 0.0594, 0.0564, 0.0537, 0.0514, 0.0495,
        0.0478, 0.0464, 0.0452, 0.0442, 0.0433, 0.0424, 0.0417, 0.0411, 0.0405,
        0.0399, 0.0394, 0.0170])
(-1 vs 1):  tensor([0.0413, 0.0522, 0.0535, 0.0522, 0.0503, 0.0487, 0.0474, 0.0466, 0.0460,
        0.0458, 0.0457, 0.0458, 0.0459, 0.0462, 0.0465, 0.0468, 0.0471, 0.0475,
        0.0479, 0.0482, 0.0484])
(0 vs 1):  tensor([0.0310, 0.0427, 0.0465, 0.0475, 0.0477, 0.0478, 0.0480, 0.0483, 0.0487,
        0.0491, 0.0495, 0.0499, 0.0503, 0.0506, 0.0509, 0.0511, 0.0513, 0.0515,
        0.0517, 0.0518, 0.0342])


In [301]:
y_pred = clf.predict(KLte) #predictions
y_score = clf.decision_function(KLte) #rank
accuracy = accuracy_score(Y_te, y_pred)
print ('Accuracy score: %.3f' % (accuracy))

(573, 3)
Accuracy score: 0.044


In [302]:
from sklearn.model_selection import KFold
cv = KFold(n_splits=5, shuffle=True, random_state=42)
mklPWMK = PWMK(delta=0, cv=cv).fit(KLtr, Y_tr)

In [303]:
y_pred = mklPWMK.predict(KLte) #predictions
y_score = mklPWMK.decision_function(KLte) #rank
accuracy = accuracy_score(Y_te, y_pred)
print ('Accuracy score: %.3f' % (accuracy))

Accuracy score: 0.358


In [304]:
mklFHeuristic = FHeuristic().fit(KLtr, Y_tr)
mklCKA = CKA().fit(KLtr, Y_tr)

In [305]:
y_pred = mklFHeuristic.predict(KLte) #predictions
y_score = mklFHeuristic.decision_function(KLte) #rank
accuracy = accuracy_score(Y_te, y_pred)
print ('Accuracy score: %.3f' % (accuracy))

Accuracy score: 0.293


In [306]:
y_pred = mklCKA.predict(KLte) #predictions
y_score = mklCKA.decision_function(KLte) #rank
accuracy = accuracy_score(Y_te, y_pred)
print ('Accuracy score: %.3f' % (accuracy))

Accuracy score: 0.297


In [307]:
y_pred = clfOVA.predict(KLte) #predictions
y_score = clfOVA.decision_function(KLte) #rank
accuracy = accuracy_score(Y_te, y_pred)
print ('Accuracy score: %.3f' % (accuracy))

Accuracy score: 0.464


In [390]:
import mkl_data_processing as mkldp
import os
import pickle
import pandas as pd
import sys
import sys
from memory_profiler import profile
import pandas as pd
import numpy as np

sys.path.append('/home/ak/Documents/Research/PaperCode/singlekernelclf/')
import jsonpickle
from MKLpy.preprocessing import normalization, rescale_01
from MKLpy.metrics import pairwise
from MKLpy import generators
from MKLpy.algorithms import AverageMKL, EasyMKL
from sklearn.svm import SVC
from collections import OrderedDict
import os
from sklearn.metrics import accuracy_score
import torch
from MKLpy.model_selection import cross_val_score
from MKLpy.multiclass import OneVsRestMKLClassifier, OneVsOneMKLClassifier
from sklearn.model_selection import train_test_split
from MKLpy.algorithms import AverageMKL, EasyMKL, \
    KOMD, HeuristicMKL, PWMK, FHeuristic, CKA  # KOMD is not a MKL algorithm but a simple kernel machine like the SVM
from MKLpy.metrics import pairwise
from MKLpy.utils.misc import identity_kernel
from fileutils import DataLoader as DataLoader
from fileutils import paths
from fileutils import new_feature_utils as nfu
from fileutils.new_feature_utils import CreateMarketFeatures
from MKLpy.model_selection import cross_val_score
from sklearn.svm import SVC
import multiprocessing

from collections import defaultdict
import os
import multiprocessing
import psutil
import itertools
import pickle
from collections import defaultdict
import itertools
import time

from MKLpy.scheduler import ReduceOnWorsening
from MKLpy.callbacks import EarlyStopping
import matplotlib.pyplot as plt


### functions ###

def open_pickle_filepath(pickle_file):
    pickle_to_file = pickle.load(open(pickle_file, "rb"), encoding='latin1')

    return pickle_to_file


def forward_Dates(list_of_keys, current_date):
    """
    return all the forward looking dates for each idxKey we use for training

    :param list_of_keys: dates i have model dates for out of sample
    :param current_date: current model date
    :return: forward dates for applying the fitted model
    """
    lookAheadKeys = sorted(i for i in list_of_keys if i > current_date)
    return lookAheadKeys


def logmemoryusage(msg):
    # function to log memory usage
    process = psutil.Process(os.getpid())
    print('Memory usage at %s is %smb.' % (msg, process.memory_info().rss / 1000 / 1000))


### paths ###

mainPath = mkldp.paths('main')

symbols = sorted(os.listdir(mkldp.paths('symbols_features')))
jointFeatureLocation = os.path.join(mainPath, "ExperimentCommonLocs/JointLocationsDicts")
commonLocs = os.path.join(mainPath, "ExperimentCommonLocs/")
# common locs contains a lot of folders, including the prediction targets and the rest

mklOOSPredictionPath = os.path.join(mainPath, "ExperimentCommonLocs/MKLOOSPredictions")
allFiles = os.listdir(jointFeatureLocation)
fittedModelsPath = os.path.join(mainPath, "ExperimentCommonLocs/FittedModels")
oosPredictionsPath = os.path.join(mainPath, "ExperimentCommonLocs/OOSPredictions")

labelsAlternateLocs = {f: os.path.join(commonLocs, f) for f in
                       os.listdir(os.path.join(mainPath, "ExperimentCommonLocs/")) if str("LabelsAlternate") in f}
labelKeys = list(labelsAlternateLocs.keys())
alternate_labels_nos = {1: "LabelsAlternateOne", 2: "LabelsAlternateTwo", 3: "LabelsAlternateThree",
                        4: "LabelsAlternateFour", 5: "LabelsAlternateFive",
                        6: "LabelsAlternateSix"}  # we have 7 alternative data types


def outer_loop_function(hmm_date):
    symbol_idx = 15  # pick a symbol - will need to iterate over a number of symbols
    label_idx = 1  # takes number 1 to 6
    symbol = sorted(symbols)[symbol_idx]  # to be serialised so read all the symbols
    print(symbol)
    symbolData = DataLoader(mainPath, symbol)  # initiate a path where all the data should be
    # this is the usual loop but we are writing it as a function so I can parallelise it
    cv_dict_list = defaultdict(dict)  # where the results are stored
    print(hmm_date)

    hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
    if os.path.isdir(hmm_features_date_path):
        symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
                                f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
        keys = sorted(list(symbol_feature_paths.keys()))
        print('For hmm date: ', hmm_date, '###########')
        for key in keys:

            print('For key: ', key, '############')
            labels_file_path = os.path.join(symbolData.symbol_specific_label_path(label_idx), key + ".csv") 
            output_dict = defaultdict(dict)

            if os.path.isfile(labels_file_path):  # check that this is a real path
                print("can train")
                print(" reading labels")  # this is the labels path!
                labels = pd.read_csv(labels_file_path)
                label_name = str(labels.columns[labels.columns.str.contains(pat='label')].values[0])
                logmemoryusage("Before garbage collect")
                hmm_features = nfu.hmm_features_df(open_pickle_filepath(symbol_feature_paths[key]))
                if hmm_features.isnull().values.all():  # checking that the HMM features are actually not null
                    continue
                    print('lots of NaNs on features')
                else:  # if features not null then start moving on!
                    market_features_df = CreateMarketFeatures(
                        CreateMarketFeatures(
                            CreateMarketFeatures(df=CreateMarketFeatures(df=labels).ma_spread_duration())
                                .ma_spread()).chaikin_mf()).obv_calc()  # market features dataframe

                    df_concat = pd.DataFrame(
                        pd.concat([hmm_features, market_features_df], axis=1, sort='False').dropna())

                    df = df_concat[df_concat[label_name].notna()]
                    df_final = df.drop(
                        columns=['TradedPrice', 'Duration', 'TradedTime', 'ReturnTradedPrice', 'Volume',
                                 label_name])

                    y_train = df.reindex(columns=df.columns[df.columns.str.contains(pat='label')])  # training labels
                    if df_final.shape[0] < 10:
                        print(' the ratio of classes is too low. try another label permutation')
                        problem_dict[hmm_date][key] = str(key)
                        continue
                    else:
                        try:
                            print("starting model fit")
                            Xtr, Xte, Ytr, Yte = train_test_split(df_final, y_train, test_size=.2, random_state=42)
                            # training
                            arrXtr = np.array(Xtr)
                            X_tr = normalization(rescale_01(arrXtr))
                            Y_tr = torch.Tensor(Ytr.values.ravel())

                            # testing

                            arrXte = np.array(Xte)
                            X_te = normalization(rescale_01(arrXte))
                            Y_te = torch.Tensor(Yte.values.ravel())

                            KLtr = [pairwise.homogeneous_polynomial_kernel(X_tr, degree=d) for d in range(1, 11)] + [
                                identity_kernel(len(Ytr))]
                            KLte = [pairwise.homogeneous_polynomial_kernel(X_te, X_tr, degree=d) for d in range(1, 11)]
                            KLte.append(torch.zeros(KLte[0].size()))
                            print('done with kernel')
                            gc.collect()
                            try:
                                lam_values = [0.1, 0.2, 1]
                                C_values = [0.01, 1, 10]
                                best_results ={}

                                # possible lambda values for the EasyMKL algorithm
                                for lam, C in itertools.product(lam_values, C_values):
                                    print('now here', C, lam)
                                    print(' and tuning lambda for EasyMKL...', end='')
                                    base_learner = SVC(C=C)  # "soft"-margin svm
                                    # MKLpy.model_selection.cross_val_score performs the cross validation automatically,
                                    # it may returns accuracy, auc, or F1 scores
                                    scores = cross_val_score(KLtr, Y_tr, EasyMKL(learner=base_learner, lam=lam), n_folds=5,
                                                             scoring='accuracy')
                                    acc = np.mean(scores)
                                    if not best_results or best_results['score'] < acc:
                                        best_results = {'lam': lam, 'score': acc}
                                    # evaluation on the test set
                                from sklearn.metrics import accuracy_score
                                print('done')

                                clf = EasyMKL(learner=base_learner, lam=lam).fit(KLtr, Ytr)

                                y_pred = clf.predict(KLte)

                                accuracy = accuracy_score(Y_te, y_pred)

                                cv_dict_list[(symbol, hmm_date, label_idx)][(lam, C)] = [scores, best_results]

                            except (ValueError, TypeError, EOFError):
                                continue
                        except (ValueError, TypeError, EOFError):
                            continue
                            logmemoryusage("at the end")
                    pickle_out_filename = os.path.join(mainPath, "ExperimentCommonLocs/MKLFittedModels", "_".join(
                        (symbol, 'model_fit_date', str(key), str(alternate_labels_nos[label_idx]), 'SingleKernelSVC.pkl')))

                    pickle_out = open(pickle_out_filename, 'wb')

                    pickle.dump(cv_dict_list, pickle_out)
                    pickle_out.close()

            else:
                print("#################### Your Labels File does not exist ----- ####")
            continue
            logmemoryusage("Before garbage collect")
    else:
        pass


if __name__ == '__main__':

    symbol_idx = 15  # pick a symbol - will need to iterate over a number of symbols
    label_idx = 1 # takes number 1 to 6

    symbol = symbols[symbol_idx]  # to be serialised so read all the symbols

    print(symbol)

    symbolData = DataLoader(mainPath, symbol)  # initiate a path where all the data should be

    labelsLocation = labelsAlternateLocs[alternate_labels_nos[label_idx]]

    labelsPath = os.path.join(labelsLocation, symbol)
    start_time = time.time()
        # this is the usual loop but we are writing it as a function so I can parallelise it
    cv_dict_list = defaultdict(dict)  # where the results are stored


    symbol_feature_paths = {feature_file.split("_")[5]: os.path.join(hmm_features_date_path, feature_file) for
                            f, feature_file in enumerate(sorted(os.listdir(hmm_features_date_path)))}
    keys = sorted(list(symbol_feature_paths.keys()))
    print('For hmm date: ', hmm_date, '###########')
    hmm_features_date_path = os.path.join(symbolData.symbol_features_path, hmm_date)
    start_time = time.time()

    with multiprocessing.Pool(processes=8) as process_pool:
        process_pool.map(outer_loop_function, sorted(symbolData.hmm_dates_list))
    current_time = time.time()
    elapsed_time = current_time - start_time
    print('elapsed time', elapsed_time)


KGF.L
LAND.L
For hmm date:  20170710 ###########
KGF.L
KGF.L
KGF.L
KGF.L
KGF.L
20170130
20170123
20170116
KGF.L
KGF.L
KGF.L
20170713
20170720
20170706
20170727
20170803
For hmm date:  20170706 ###########
For hmm date:  20170130 ###########
For key:  20170707 ############
For key:  20170131 ############
can train
can train
 reading labels
 reading labels
Memory usage at Before garbage collect is 4130.9962239999995mb.
Memory usage at Before garbage collect is 4130.971648mb.
For hmm date:  20170116 ###########
For key:  20170117 ############
can train
 reading labels
Memory usage at Before garbage collect is 4130.9184mb.
For hmm date:  20170720 ###########
For key:  20170721 ############
can train
 reading labels
For hmm date:  20170727 ###########
For key:  20170728 ############
can train
 reading labels
Memory usage at Before garbage collect is 4130.967552mb.
Memory usage at Before garbage collect is 4130.971648mb.
For hmm date:  20170713 ###########
For key:  20170714 ############
can

Memory usage at Before garbage collect is 4131.49184mb.
For key:  20170727 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.422208mb.
For key:  20170131 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.405824mb.
For key:  20170706 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.328mb.
Memory usage at Before garbage collect is 4134.109184mb.
For key:  20170803 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.500032mb.
For key:  20170728 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.504128mb.
For key:  20170810 ############
can train
 reading labels
For key:  20170821 ############
can train
 reading labels
Memory usage at Before garbage collect is 4138.487808mb.
For key:  20170731 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.504128mb.
For key:  20170804 ########

For key:  20170815 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.590144mb.
For key:  20170906 ############
can train
 reading labels
Memory usage at Before garbage collect is 4135.50592mb.
Memory usage at Before garbage collect is 4138.860544mb.
For key:  20170907 ############
can train
 reading labels
For key:  20170804 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.520512mb.
For key:  20170817 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.516416mb.
For key:  20170714 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.446784mb.
For key:  20170907 ############
can train
 reading labels
Memory usage at Before garbage collect is 4138.860544mb.
Memory usage at Before garbage collect is 4135.50592mb.
For key:  20170908 ############
can train
 reading labels
For key:  20170818 ############
can train
 reading labels
Memory usage at Before g

For key:  20170905 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.672063999999mb.
For key:  20170825 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.762176mb.
For key:  20170719 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.5368960000005mb.
For key:  20170919 ############
can train
 reading labels
Memory usage at Before garbage collect is 4140.150784mb.
For key:  20170727 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.651584mb.
For key:  20170831 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.635200000001mb.
For key:  20170906 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.753984mb.
For key:  20170918 ############
can train
 reading labels
Memory usage at Before garbage collect is 4135.673856mb.
For key:  20170728 ############
can train
 reading labels
Mem

can train
 reading labels
Memory usage at Before garbage collect is 4140.978176mb.
For key:  20170803 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.5368960000005mb.
For key:  20170911 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.766272mb.
For key:  20170831 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.667968mb.
For key:  20170927 ############
can train
 reading labels
Memory usage at Before garbage collect is 4139.323392mb.
For key:  20170810 ############
can train
 reading labels
Memory usage at Before garbage collect is 4131.651584mb.
For key:  20170927 ############
can train
 reading labels
Memory usage at Before garbage collect is 4141.19936mb.
For key:  20170804 ############
can train
 reading labels
For key:  20170918 ############
can train
Memory usage at Before garbage collect is 4131.5368960000005mb.
 reading labels
Memory usage at Before garbage collect is

...

 and tuning lambda for EasyMKL...now here 1 0.1
starting model fit
For key:  20180221 ############
can train
 reading labels
Memory usage at Before garbage collect is 4140.032mb.
 and tuning lambda for EasyMKL...done
For key:  20170831 ############
done with kernel
can train
 reading labels
Memory usage at Before garbage collect is 4932.943872000001mb.
 and tuning lambda for EasyMKL...done
For key:  20170929 ############
can train
 reading labels
Memory usage at Before garbage collect is 5037.584384mb.


Process ForkPoolWorker-380:
Process ForkPoolWorker-383:
Process ForkPoolWorker-382:
Process ForkPoolWorker-384:
Traceback (most recent call last):
Traceback (most recent call last):
Traceback (most recent call last):
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/pool.py", line 119, in worker
    result = (True, func(*args, **kwds))
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/usr/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/lib/python3.6/mul

 and tuning lambda for EasyMKL...

  File "/home/ak/Envs/resrPyth3/lib/python3.6/site-packages/MKLpy/model_selection.py", line 31, in <listcomp>
    KLtr = [K[train][:,train] for K in KL]
  File "/home/ak/Envs/resrPyth3/lib/python3.6/site-packages/MKLpy/model_selection.py", line 31, in cross_val_score
    KLtr = [K[train][:,train] for K in KL]


KeyboardInterrupt: 

In [374]:
# hmm_features_date_path = os.path.join(, hmm_date)
symbolData.symbol_features_path
hmm_date

'20170118'

In [344]:
# somelists = [   
#      [16, 17],  # pick a symbol - will need to iterate over a number of symbols
#      [ 1, 2, 3, 4, 5, 6],  # takes number 1 to 6
#      [sorted(symbolData.hmm_dates_list)]
# ]
# for element in itertools.product(*somelists):
#     print(element)

In [347]:
import functools.partial
def f(a, b, c):
    print("{} {} {}".format(a, b, c))

def main():
    iterable = [1, 2, 3, 4, 5]
    pool = multiprocessing.Pool()
    a = "hi"
    b = "there"
    func = partial(f, a, b)
    pool.map(func, iterable)
    pool.close()
    pool.join()

if __name__ == "__main__":
    main()

ModuleNotFoundError: No module named 'functools.partial'; 'functools' is not a package